In [88]:
import numpy as np
import h5py
import glob
from pycbc import pnutils
from pycbc import catalog

In [2]:
file = glob.glob('./ringdown_config_file/*.ini')

In [3]:
name = []
for f in file:
    name.append(f.split('-')[1][:15])

In [4]:
name.sort()

In [30]:
f = h5py.File('/work/yifan.wang/4ogc/LVK/GWTC-3/IGWN-GWTC3p0-v1-GW191103_012549_PEDataRelease_mixed_cosmo.h5','r')

In [95]:
c = catalog.Catalog(source='gwtc-3')

In [107]:
c.names

dict_keys(['GW191103_012549-v1', 'GW191105_143521-v1', 'GW191109_010717-v1', 'GW191113_071753-v1', 'GW191126_115259-v1', 'GW191127_050227-v1', 'GW191129_134029-v1', 'GW191204_110529-v1', 'GW191204_171526-v1', 'GW191215_223052-v1', 'GW191216_213338-v1', 'GW191219_163120-v1', 'GW191222_033537-v1', 'GW191230_180458-v1', 'GW200112_155838-v1', 'GW200115_042309-v2', 'GW200128_022011-v1', 'GW200129_065458-v1', 'GW200202_154313-v1', 'GW200208_130117-v1', 'GW200208_222617-v1', 'GW200209_085452-v1', 'GW200210_092254-v1', 'GW200216_220804-v1', 'GW200219_094415-v1', 'GW200220_061928-v1', 'GW200220_124850-v1', 'GW200224_222234-v1', 'GW200225_060421-v1', 'GW200302_015811-v1', 'GW200306_093714-v1', 'GW200308_173609-v1', 'GW200311_115853-v1', 'GW200316_215756-v1', 'GW200322_091133-v1'])

In [115]:
c.data['GW191103_012549-v1']['strain'][0]['detector']

'H1'

In [119]:
len(c.data['GW191103_012549-v1']['strain'])

24

In [147]:
def detinfo(name):
    if name == 'GW200115_042309':
        name=name+'-v2'
    else:
        name = name + '-v1'
    det = []
    for i in range(len(c.data[name]['strain'])):
        det.append(c.data[name]['strain'][i]['detector'])
    det = list(set(det))
    return det

In [148]:
def info(name):
    h5file = glob.glob('/work/yifan.wang/4ogc/LVK/GWTC-3/*'+str(name)+'*_cosmo.h5')
    f = h5py.File(h5file[0],'r')
    # ra, dec, mass
    ra = np.median(f['C01:Mixed']['posterior_samples']['ra'])
    dec = np.median(f['C01:Mixed']['posterior_samples']['dec'])
    final_mass_low = np.quantile(f['C01:Mixed']['posterior_samples']['final_mass'],0.01) 
    final_mass_high = np.quantile(f['C01:Mixed']['posterior_samples']['final_mass'],0.99)    # final_frequency
    m1 = np.median(f['C01:Mixed']['posterior_samples']['mass_1'])
    m2 = np.median(f['C01:Mixed']['posterior_samples']['mass_2'])
    spin1z = np.median(f['C01:Mixed']['posterior_samples']['spin_1z'])
    spin2z = np.median(f['C01:Mixed']['posterior_samples']['spin_1z'])
    final_freq = pnutils.get_final_freq('SEOBNRv4',m1,m2,spin1z,spin2z)
    f.close()
    return ra,dec,final_mass_low,final_mass_high,final_freq

In [150]:
with open('events.ini', 'w') as t:
    for ii in name:
        print(ii)
        ra,dec,final_mass_low,final_mass_high,final_freq = info(ii)
        filedir = glob.glob('./ringdown_config_file/*'+str(ii)+'*.ini')[0]
        t.write('[event-'+str(ii)+']\n')
        t.write('label='+str(ii)+'\n')
        t.write('config-files='+str(filedir)+'\n\t\t\tkerr_base.ini\n')
        t.write('config-overrides =static_params:ra:'+str(ra)+'\n')
        t.write('\t\t\tstatic_params:dec:'+str(dec)+'\n')
        t.write('\t\t\tprior-final_mass:min-final_mass:'+str(final_mass_low)+'\n')
        t.write('\t\t\tprior-final_mass:max-final_mass:'+str(final_mass_high)+'\n')
        if final_freq > 512 and final_freq < 1024:
            t.write('\t\t\tdata:sample-rate:2048\n')
        elif final_freq > 1024:
            t.write('\t\t\tdata:sample-rate:4096\n')
            
        if ii=='GW191109_010717' or ii=='GW191113_071753':
            t.write('\t\t\tdata:psd-start-time:H1:-100,L1:-256\n')
            t.write('\t\t\tdata:psd-end-time:H1:412,L1:-256\n')
        print(detinfo(ii))
        if detinfo(ii)==['H1','L1']:
            t.write('\t\t\tdata:data-conditioning-low-freq:"H1:0 L1:0"\n')
        if detinfo(ii)==['H1','V1']:
            t.write('\t\t\tdata:data-conditioning-low-freq:"H1:0 V1:0"\n')
        if detinfo(ii)==['L1','V1']:
            t.write('\t\t\tdata:data-conditioning-low-freq:"L1:0 V1:0"\n')
        t.write('\n')
t.close()

GW191103_012549
['H1', 'L1']
GW191105_143521
['H1', 'V1', 'L1']
GW191109_010717
['H1', 'L1']
GW191113_071753
['H1', 'V1', 'L1']
GW191126_115259
['H1', 'L1']
GW191127_050227
['H1', 'V1', 'L1']
GW191129_134029
['H1', 'L1']
GW191204_110529
['H1', 'L1']
GW191204_171526
['H1', 'L1']
GW191215_223052
['H1', 'V1', 'L1']
GW191216_213338
['H1', 'V1']
GW191219_163120
['H1', 'V1', 'L1']
GW191222_033537
['H1', 'L1']
GW191230_180458
['H1', 'V1', 'L1']
GW200112_155838
['L1', 'V1']
GW200115_042309
['H1', 'V1', 'L1']
GW200128_022011
['H1', 'L1']
GW200129_065458
['H1', 'V1', 'L1']
GW200202_154313
['H1', 'V1', 'L1']
GW200208_130117
['H1', 'V1', 'L1']
GW200208_222617
['H1', 'V1', 'L1']
GW200209_085452
['H1', 'V1', 'L1']
GW200210_092254
['H1', 'V1', 'L1']
GW200216_220804
['H1', 'V1', 'L1']
GW200219_094415
['H1', 'V1', 'L1']
GW200220_061928
['H1', 'V1', 'L1']
GW200220_124850
['H1', 'L1']
GW200224_222234
['H1', 'V1', 'L1']
GW200225_060421
['H1', 'L1']
GW200302_015811
['H1', 'V1']
GW200306_093714
['H1', 'L1']